## Self borrowing activity on Compound V2

This notebook intends to illustrate the correlation between self-borrowing and the incentives intern to the protocol. 

In [1]:
import altair as alt
alt.data_transformers.disable_max_rows()
import pandas as pd
import numpy as np
import statsmodels.api as sm
from datetime import datetime


In [2]:
liability_matrix = pd.read_csv('../data/balance_sheets/daily_liability_matrix.csv')
liability_matrix = liability_matrix.rename(columns={'date': 'timestamp'})
liability_matrix['timestamp'] = pd.to_datetime(liability_matrix['timestamp'])
liability_matrix.set_index('timestamp', inplace=True)
liability_matrix

symbol_bor symbol_col  account  matchBorrowUSD  matchCollateralUSD  \
timestamp                                                                       
2019-05-07       cBAT       cBAT        1    1.028105e+01        1.763471e+02   
2019-05-07       cBAT       cETH        2    1.895208e+01        3.152674e+02   
2019-05-07       cBAT       cREP        1    2.004187e+00        3.437709e+01   
2019-05-07       cBAT       cSAI        1    2.686493e+01        4.608043e+02   
2019-05-07       cBAT      cUSDC        1    8.139770e+00        1.396185e+02   
...               ...        ...      ...             ...                 ...   
2023-12-31       cZRX      cUSDC       50    2.480400e+03        4.436415e+03   
2023-12-31       cZRX      cWBTC       15    2.216448e+02        5.437547e+02   
2023-12-31       cZRX     cWBTC2       12    3.981955e+02        5.874706e+02   
2023-12-31       cZRX       cYFI        1    1.769349e-09        1.811555e-05   
2023-12-31       cZRX       cZRX       26    9.558008e+04        1.129690e+06   

            effectiveUSD  
timestamp                 
2019-05-07  1.028105e+01  
2019-05-07  1.895208e+01  
2019-05-07  2.004187e+00  
2019-05-07  2.686493e+01  
2019-05-07  8.139770e+00  
...                  ...  
2023-12-31  2.476376e+03  
2023-12-31  2.126259e+02  
2023-12-31  3.548962e+02  
2023-12-31  1.769349e-09  
2023-12-31  9.558008e+04  

[243343 rows x 6 columns]

In [3]:
self_borrow = liability_matrix[liability_matrix['symbol_bor'] == liability_matrix['symbol_col']]
self_borrow = self_borrow.groupby(['symbol_bor', 'timestamp']).sum().drop(['symbol_col', 'account', 'effectiveUSD', 'matchCollateralUSD'], axis=1).reset_index()
self_borrow.set_index('timestamp', inplace=True)
self_borrow = self_borrow.rename(columns={'matchBorrowUSD': 'selfBorrowUSD'})
self_borrow

symbol_bor  selfBorrowUSD
timestamp                           
2021-08-19      cAAVE    2489.868402
2021-08-20      cAAVE    2722.808655
2021-08-21      cAAVE    4610.444347
2021-08-22      cAAVE    4503.303663
2021-08-23      cAAVE    4627.488659
...               ...            ...
2023-12-27       cZRX   94198.865395
2023-12-28       cZRX   94199.987140
2023-12-29       cZRX   94214.602510
2023-12-30       cZRX   95575.158051
2023-12-31       cZRX   95580.078676

[16866 rows x 2 columns]

In [4]:
total_borrow = liability_matrix.groupby('timestamp').sum().drop(['symbol_col', 'account', 'effectiveUSD', 'symbol_bor'], axis=1)
total_borrow = total_borrow.rename(columns={'matchBorrowUSD': 'totalBorrowUSD', 'matchCollateralUSD': 'totalCollateralUSD'})
total_borrow

totalBorrowUSD  totalCollateralUSD
timestamp                                     
2019-05-07    5.869795e+02        1.005838e+04
2019-05-08    4.718694e+03        1.258688e+04
2019-05-09    5.818155e+03        1.258489e+04
2019-05-10    5.852302e+03        1.158306e+04
2019-05-11    6.179203e+03        1.246662e+04
...                    ...                 ...
2023-12-27    4.479141e+08        1.156537e+09
2023-12-28    4.386121e+08        1.121863e+09
2023-12-29    4.380012e+08        1.096472e+09
2023-12-30    4.366821e+08        1.100737e+09
2023-12-31    4.363781e+08        1.101058e+09

[1700 rows x 2 columns]

In [5]:
borrowings = self_borrow.merge(total_borrow, how='left', on='timestamp')
borrowings['selfBorrowUSD'] = borrowings['selfBorrowUSD'].fillna(0) 
borrowings['selfBorrowShare'] = borrowings["selfBorrowUSD"] / borrowings["totalBorrowUSD"]
borrowings

symbol_bor  selfBorrowUSD  totalBorrowUSD  totalCollateralUSD  \
timestamp                                                                  
2021-08-19      cAAVE    2489.868402    7.914928e+09        1.444673e+10   
2021-08-20      cAAVE    2722.808655    8.025064e+09        1.487075e+10   
2021-08-21      cAAVE    4610.444347    8.088935e+09        1.506277e+10   
2021-08-22      cAAVE    4503.303663    8.091316e+09        1.503731e+10   
2021-08-23      cAAVE    4627.488659    8.139425e+09        1.519342e+10   
...               ...            ...             ...                 ...   
2023-12-27       cZRX   94198.865395    4.479141e+08        1.156537e+09   
2023-12-28       cZRX   94199.987140    4.386121e+08        1.121863e+09   
2023-12-29       cZRX   94214.602510    4.380012e+08        1.096472e+09   
2023-12-30       cZRX   95575.158051    4.366821e+08        1.100737e+09   
2023-12-31       cZRX   95580.078676    4.363781e+08        1.101058e+09   

            selfBorrowShare  
timestamp                    
2021-08-19     3.145788e-07  
2021-08-20     3.392881e-07  
2021-08-21     5.699693e-07  
2021-08-22     5.565601e-07  
2021-08-23     5.685277e-07  
...                     ...  
2023-12-27     2.103057e-04  
2023-12-28     2.147683e-04  
2023-12-29     2.151013e-04  
2023-12-30     2.188667e-04  
2023-12-31     2.190304e-04  

[16866 rows x 5 columns]

In [69]:
a = borrowings.reset_index()
a[a['timestamp'] == '2021-08-09']

timestamp symbol_bor  selfBorrowUSD  totalBorrowUSD  \
1601  2021-08-09       cBAT   7.305754e+06    7.794156e+09   
2772  2021-08-09      cCOMP   1.114308e+07    7.794156e+09   
4245  2021-08-09       cDAI   2.620342e+09    7.794156e+09   
5945  2021-08-09       cETH   2.167136e+08    7.794156e+09   
9718  2021-08-09       cUNI   5.410635e+06    7.794156e+09   
11349 2021-08-09      cUSDC   2.350933e+09    7.794156e+09   
12615 2021-08-09      cWBTC   2.229453e+03    7.794156e+09   
13633 2021-08-09     cWBTC2   1.532806e+08    7.794156e+09   
15991 2021-08-09       cZRX   1.826946e+07    7.794156e+09   

       totalCollateralUSD  selfBorrowShare  
1601         1.445106e+10     9.373373e-04  
2772         1.445106e+10     1.429672e-03  
4245         1.445106e+10     3.361931e-01  
5945         1.445106e+10     2.780463e-02  
9718         1.445106e+10     6.941912e-04  
11349        1.445106e+10     3.016277e-01  
12615        1.445106e+10     2.860416e-07  
13633        1.445106e+10     1.966609e-02  
15991        1.445106e+10     2.343995e-03

In [6]:
df = borrowings[borrowings['symbol_bor'].isin(['cUSDC', 'cCOMP', 'cDAI', 'cETH', 'cZRX', 'cWBTC2'])]

alt.Chart(df.reset_index()).mark_bar().encode(
    x='timestamp:T',
    y='selfBorrowShare',
    color='symbol_bor'
).interactive(bind_y = False)

alt.Chart(...)

Little historical view regarding the rewards:

- **June 15th, 2020**: Every Ethereum block, 0.50 COMP will be distributed across ETH, DAI, USDC, USDT, BAT, REP, WBTC and ZRX markets

- **June 27th, 2020**: Lower the number of distributed COMP to 0.44

- **August 31st, 2020**: Reduce COMP emissions by 20%

- **October 17th, 2020**: Add COMP Support

- **September 29th, 2021**: two different COMP distribution rates for each and every market - borrow-side rate and supply-side rate.

- **November 12th, 2021**: End cCOMP Borrow Rewards

- **March 27th, 2022**: the governance has voted to cut the existing rewards by 50%

- **June 29th, 2023**: Top-up COMP Rewards

## COMP Price

In [7]:
comp = pd.read_csv('../data/COMP_USD.csv', sep=';')

comp.head()

timeOpen                 timeClose  \
0  2024-02-08T00:00:00.000Z  2024-02-08T23:59:59.999Z   
1  2024-02-07T00:00:00.000Z  2024-02-07T23:59:59.999Z   
2  2024-02-06T00:00:00.000Z  2024-02-06T23:59:59.999Z   
3  2024-02-05T00:00:00.000Z  2024-02-05T23:59:59.999Z   
4  2024-02-04T00:00:00.000Z  2024-02-04T23:59:59.999Z   

                   timeHigh                   timeLow  name       open  \
0  2024-02-08T23:19:00.000Z  2024-02-08T12:53:00.000Z  2781  53.210016   
1  2024-02-07T20:50:00.000Z  2024-02-07T08:14:00.000Z  2781  52.522981   
2  2024-02-06T13:55:00.000Z  2024-02-06T14:16:00.000Z  2781  52.186594   
3  2024-02-05T13:40:00.000Z  2024-02-05T01:16:00.000Z  2781  53.479430   
4  2024-02-04T00:05:00.000Z  2024-02-04T22:43:00.000Z  2781  54.883572   

        high        low      close       volume     marketCap  \
0  54.087003  53.195422  53.991065  27736555.03  4.357963e+08   
1  53.555882  52.007126  53.210343  27746092.59  4.294929e+08   
2  53.102701  52.098893  52.523693  31031166.03  4.239104e+08   
3  53.512569  52.058446  52.185942  30687682.36  4.211833e+08   
4  54.900357  53.094205  53.497120  38982054.06  4.317643e+08   

                  timestamp  
0  2024-02-08T23:59:59.999Z  
1  2024-02-07T23:59:59.999Z  
2  2024-02-06T23:59:59.999Z  
3  2024-02-05T23:59:59.999Z  
4  2024-02-04T23:59:59.999Z

In [8]:
alt.Chart(comp).mark_line().encode(
    x='timestamp:T',
    y='close:Q'
).interactive(bind_y = False)

alt.Chart(...)

In [9]:
price = comp[['timestamp', 'close']]
price['timestamp'] = price['timestamp'].apply(lambda date: datetime.strptime(date, '%Y-%m-%dT%H:%M:%S.%fZ'))
price['timestamp'] = price['timestamp'].dt.strftime('%Y-%m-%d')
price['timestamp'] = pd.to_datetime(price['timestamp'])
price = price.rename(columns={'close': 'USD_price'})
price.set_index('timestamp', inplace=True)

price

/tmp/ipykernel_113085/449598176.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  price['timestamp'] = price['timestamp'].apply(lambda date: datetime.strptime(date, '%Y-%m-%dT%H:%M:%S.%fZ'))
/tmp/ipykernel_113085/449598176.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  price['timestamp'] = price['timestamp'].dt.strftime('%Y-%m-%d')
/tmp/ipykernel_113085/449598176.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] =

USD_price
timestamp             
2024-02-08   53.991065
2024-02-07   53.210343
2024-02-06   52.523693
2024-02-05   52.185942
2024-02-04   53.497120
...                ...
2020-06-20  258.911624
2020-06-19  224.545206
2020-06-18  148.669784
2020-06-17   64.635640
2020-06-16   93.198607

[1333 rows x 1 columns]

In [10]:
price['price_variation (%)'] = (price['USD_price'] - price['USD_price'].shift(1)) / price['USD_price'].shift(1)
price

USD_price  price_variation (%)
timestamp                                  
2024-02-08   53.991065                  NaN
2024-02-07   53.210343            -0.014460
2024-02-06   52.523693            -0.012904
2024-02-05   52.185942            -0.006430
2024-02-04   53.497120             0.025125
...                ...                  ...
2020-06-20  258.911624            -0.231823
2020-06-19  224.545206            -0.132734
2020-06-18  148.669784            -0.337907
2020-06-17   64.635640            -0.565240
2020-06-16   93.198607             0.441907

[1333 rows x 2 columns]

In [11]:
alt.Chart(price.reset_index()).mark_line().encode(
    x='timestamp:T',
    y='price_variation (%):Q'
).interactive(bind_y = False)

alt.Chart(...)

# Fees 

In [12]:
markets = pd.read_csv('../data/balance_sheets/daily_markets.csv')

markets

borrowRate          cash  collateralFactor  exchangeRate  \
0        0.039471  1.440748e+01              0.50      0.020000   
1        0.016183  1.135850e+03              0.75      0.020000   
2        0.012274  1.530022e+01              0.75      0.020000   
3        0.033222  4.381321e+03              0.60      0.020000   
4        0.054585  7.674348e+02              0.60      0.020000   
...           ...           ...               ...           ...   
24015    0.020854  1.079928e+04              0.70      0.020077   
24016    0.063432  2.843612e+03              0.53      0.020652   
24017    0.050184  1.677910e+05              0.00      0.021450   
24018    0.060570  4.332347e+07              0.00      0.022917   
24019    0.029136  2.586894e+05              0.59      0.020214   

                         interestRateModelAddress  \
0      0xbae04cbf96391086dc643e842b517734e214d698   
1      0xc64c4cba055efa614ce01f4bad8a9f519c4f8fab   
2      0xc64c4cba055efa614ce01f4bad8a9f519c4f8fab   
3      0xbae04cbf96391086dc643e842b517734e214d698   
4      0xbae04cbf96391086dc643e842b517734e214d698   
...                                           ...   
24015  0xf2e5db36b0682f2cd6bc805c3a4236194e01f4d5   
24016  0xd956188795ca6f4a74092ddca33e0ea4ca3a1395   
24017  0xa1046abfc2598f48c44fb320d281d3f3c0733c9a   
24018  0xfb564da37b41b2f6b6edcc3e56fbf523bd9f2012   
24019  0xd956188795ca6f4a74092ddca33e0ea4ca3a1395   

                                 name      reserves  supplyRate  symbol  \
0                      Compound Augur  0.000000e+00    0.002306    cREP   
1                   Compound USD Coin  6.000000e-06    0.001179   cUSDC   
2                      Compound Ether  4.704680e-06    0.000678    cETH   
3      Compound Basic Attention Token  4.561337e-04    0.001318    cBAT   
4                         Compound 0x  1.724746e-04    0.005664    cZRX   
...                               ...           ...         ...     ...   
24015            Compound Wrapped BTC  1.209393e+02    0.000063  cWBTC2   
24016             Compound Aave Token  7.554810e+02    0.009183   cAAVE   
24017                    Compound Dai  1.618363e+01    0.000000    cSAI   
24018                   Compound USDT  3.998687e+06    0.045879   cUSDT   
24019        Compound ChainLink Token  1.229466e+04    0.000887   cLINK   

                                    cTokenAddress  ...  underlyingPrice  \
0      0x158079ee67fce2f58472a96584a73c7ab9ac95c1  ...         0.116547   
1      0x39aa39c021dfbae8fac545936693ac917d5e7563  ...         0.005846   
2      0x4ddc2d193948926d02f9b1fe9e1daa0718270ed5  ...         1.000000   
3      0x6c8c6b02e7b2be14d4fa6022dfd6d75921d90e4e  ...         0.001898   
4      0xb3319f5d18bc0d84dd1b4825dcde5d5f7266d407  ...         0.001559   
...                                           ...  ...              ...   
24015  0xccf4429db6322d5c611ee964527d42e5d685dd6a  ...        18.639788   
24016  0xe65cdb6479bac1e22340e4e755fae7e509ecd06c  ...         0.050658   
24017  0xf5dce57282a584d2746faf1593d3121fcac444dc  ...         0.005285   
24018  0xf650c3d88d12db855b8bf7d11be6c55a4e07dcc9  ...         0.000439   
24019  0xface851a4921ce59e912d19329929ce6da6eb0c7  ...         0.006718   

       underlyingSymbol accrualBlockNumber blockTimestamp  borrowIndex  \
0                   REP            7715069     1557250486     1.000041   
1                  USDC            7716064     1557264374     1.000001   
2                   ETH            7716242     1557266749     1.000047   
3                   BAT            7712572     1557217208     1.000026   
4                   ZRX            7711781     1557206685     1.000021   
...                 ...                ...            ...          ...   
24015              WBTC           18908253     1704059495     1.099060   
24016              AAVE           18905443     1704025487     1.184327   
24017               DAI           18845375     1704024035     1.427331   
24018              USDT

In [13]:
fees = []
for symbol in markets['symbol'].unique():
    asset_fees = markets[markets['symbol'] == symbol]
    asset_fees['fee_variation (%)'] = (asset_fees['borrowRate'] - asset_fees['borrowRate'].shift(1)) / asset_fees['borrowRate'].shift(1)

    fees.append(asset_fees) 

fees = pd.concat(fees)[['symbol', 'fee_variation (%)', 'borrowRate', 'date']]
fees = fees.rename(columns={'date': 'timestamp'})
fees['timestamp'] = pd.to_datetime(fees['timestamp'])
fees.set_index('timestamp', inplace=True)

fees.head()

/tmp/ipykernel_113085/2717390549.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  asset_fees['fee_variation (%)'] = (asset_fees['borrowRate'] - asset_fees['borrowRate'].shift(1)) / asset_fees['borrowRate'].shift(1)
/tmp/ipykernel_113085/2717390549.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  asset_fees['fee_variation (%)'] = (asset_fees['borrowRate'] - asset_fees['borrowRate'].shift(1)) / asset_fees['borrowRate'].shift(1)
/tmp/ipykernel_113085/2717390549.py:4: SettingWithCopyWarning: 
A value is t

symbol  fee_variation (%)  borrowRate
timestamp                                       
2019-05-07   cREP                NaN    0.039471
2019-05-08   cREP                0.0    0.039471
2019-05-09   cREP                0.0    0.039471
2019-05-10   cREP                0.0    0.039471
2019-05-11   cREP                0.0    0.039471

In [14]:
df = fees[fees['symbol'].isin(['cUSDC', 'cCOMP', 'cDAI', 'cETH', 'cZRX', 'cWBTC2'])]

alt.Chart(df.reset_index()).mark_line().encode(
    x='timestamp:T',
    y='fee_variation (%)',
    color='symbol'
).interactive(bind_y = False)

alt.Chart(...)

# TVL

In [66]:
import json

json_file = 'daily_TVL.json'

with open(json_file, 'r') as f:
    data = json.load(f)

tvl = []
for entry in data['tvl']:
    tvl.append({'TVL': entry['totalLiquidityUSD']})

tvl = pd.DataFrame(tvl)
end_date = pd.to_datetime('2024-02-28')
start_date = end_date - pd.Timedelta(days=len(tvl) - 1)
tvl['timestamp'] = pd.date_range(start=start_date, end=end_date, freq='D')
tvl.set_index('timestamp', inplace=True)

start_date = pd.to_datetime('2021-08-19')
end_date = pd.to_datetime('2023-07-31')

tvl = tvl.reset_index()
tvl = tvl[tvl['timestamp'].between(start_date, end_date)]

tvl.head()

timestamp           TVL
1046 2021-08-19  1.037066e+10
1047 2021-08-20  1.024546e+10
1048 2021-08-21  1.025178e+10
1049 2021-08-22  1.029383e+10
1050 2021-08-23  1.014308e+10

In [67]:
alt.Chart(tvl.reset_index()).mark_line().encode(
    x='timestamp:T',
    y='TVL:Q'
).interactive(bind_y = False)

alt.Chart(...)

In [57]:
selfBorrowShare= borrowings.groupby('timestamp').sum().drop('symbol_bor', axis=1)
selfBorrowShare['selfBorrowShare'] = selfBorrowShare["selfBorrowUSD"] / selfBorrowShare["totalBorrowUSD"]
selfBorrowShare = selfBorrowShare.reset_index()
selfBorrowShare = selfBorrowShare[selfBorrowShare['timestamp'].between(start_date, end_date)]
selfBorrowShare

timestamp  selfBorrowUSD  totalBorrowUSD  totalCollateralUSD  \
835  2021-08-19   5.416844e+09    8.706421e+10        1.589140e+11   
836  2021-08-20   5.411134e+09    9.630077e+10        1.784490e+11   
837  2021-08-21   5.430208e+09    9.706722e+10        1.807533e+11   
838  2021-08-22   5.400847e+09    9.709580e+10        1.804477e+11   
839  2021-08-23   5.333646e+09    9.767310e+10        1.823211e+11   
...         ...            ...             ...                 ...   
1542 2023-07-27   1.336131e+08    7.405457e+09        1.636814e+10   
1543 2023-07-28   1.352411e+08    7.434695e+09        1.649198e+10   
1544 2023-07-29   1.354130e+08    7.443067e+09        1.649062e+10   
1545 2023-07-30   1.344180e+08    7.251096e+09        1.608796e+10   
1546 2023-07-31   1.341526e+08    7.402405e+09        1.644150e+10   

      selfBorrowShare  
835          0.062217  
836          0.056190  
837          0.055943  
838          0.055624  
839          0.054607  
...               ...  
1542         0.018043  
1543         0.018191  
1544         0.018193  
1545         0.018538  
1546         0.018123  

[712 rows x 5 columns]

In [58]:
alt.Chart(selfBorrowShare).mark_line().encode(
    x='timestamp:T',
    y='selfBorrowShare:Q'
).interactive(bind_y = False)

alt.Chart(...)

In [60]:
price_filtered = price.reset_index()
price_filtered = price_filtered[price_filtered['timestamp'].between(start_date, end_date)]
price_filtered

timestamp   USD_price  price_variation (%)
192 2023-07-31   66.138300             0.007298
193 2023-07-30   71.036632             0.074062
194 2023-07-29   72.280781             0.017514
195 2023-07-28   72.094845            -0.002572
196 2023-07-27   70.095282            -0.027735
..         ...         ...                  ...
899 2021-08-23  465.558598             0.099911
900 2021-08-22  460.365323            -0.011155
901 2021-08-21  462.325055             0.004257
902 2021-08-20  480.044869             0.038328
903 2021-08-19  457.666976            -0.046616

[712 rows x 3 columns]

In [62]:
alt.Chart(price_filtered).mark_line().encode(
    x='timestamp:T',
    y='USD_price:Q'
).interactive(bind_y = False)

alt.Chart(...)

In [71]:
from sklearn.preprocessing import StandardScaler

start_date = pd.to_datetime('2021-08-19')
end_date = pd.to_datetime('2023-07-31')


#'cUSDC', 'cCOMP', 'cETH', 'cDAI', 'cZRX', 'cWBTC2'
price_filtered = price.reset_index()
price_filtered = price_filtered[price_filtered['timestamp'].between(start_date, end_date)]

def get_single_regression():
    X = price_filtered['USD_price']
    X  = X.reset_index(drop=True)
    Y  = selfBorrowShare.reset_index(drop=True)
    X1 = tvl.loc[start_date:end_date]['TVL'].reset_index(drop=True)

    """ Scale the predictor variables: If the predictor variables have different scales, 
    it can lead to numerical instability in the computations. To address this, you can 
    scale the predictor variables to have mean 0 and standard deviation 1. This is known as standardization. """ 
    
    scaler = StandardScaler()
    X_scaled = scaler.fit_transform(X.to_frame())
   

    single_model = sm.OLS(Y, sm.add_constant(X)).fit()
    print(single_model.summary())

get_single_regression()

TypeError: '<' not supported between instances of 'int' and 'Timestamp'

Make a table and the regression with as many variables as possible to know wich variables

In [ ]:
start_date = pd.to_datetime('2021-08-19')
end_date = pd.to_datetime('2023-07-31')

price_filtered = price.reset_index()
price_filtered = price_filtered[price_filtered['timestamp'].between(start_date, end_date)]

def get_multi_regression(symbol):
    Y = borrowings.groupby('symbol_bor').get_group(symbol).loc[start_date:end_date]['selfBorrowShare']

    X1 = tvl.loc[start_date:end_date]['TVL']
    scaler = StandardScaler()
    X1_scaled = scaler.fit_transform(X1.to_frame())

    X2 = price_filtered['price_variation (%)']
    X3 = price_filtered['USD_price']
    X4 = fees.groupby('symbol').get_group(symbol).loc[start_date:end_date]['fee_variation (%)']
    X5 = fees.groupby('symbol').get_group(symbol).loc[start_date:end_date]['borrowRate']

    multi_model = sm.OLS(Y, sm.add_constant(np.column_stack((X3, X5)))).fit()
    print(multi_model.summary())

get_multi_regression('cZRX')

                            OLS Regression Results                            
Dep. Variable:        selfBorrowShare   R-squared:                       0.836
Model:                            OLS   Adj. R-squared:                  0.835
Method:                 Least Squares   F-statistic:                     1803.
Date:                Thu, 14 Mar 2024   Prob (F-statistic):          9.72e-279
Time:                        15:38:29   Log-Likelihood:                 4647.2
No. Observations:                 712   AIC:                            -9288.
Df Residuals:                     709   BIC:                            -9275.
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const         -0.0016   4.96e-05    -32.956      0.0